In [1]:
import pandas as pd

In [5]:
stations = pd.read_csv('../data/stations/treated_data/2021.11.08_Endereços-BikeSAMPA.csv')
stations = stations.rename(columns={'NÚMERO ESTAÇÃO':'id', 'LATITUDE (SIG 4326)':'lat',
                                    'LONGITUDE (SIG 4326)':'lon'})
stations

Unnamed: 0   id                     NOME  \
0             0    1          Largo da Batata   
1             1    2           SESC Pinheiros   
2             2    3           CPTM Pinheiros   
3             3    4        Rua Diogo Moreira   
4             4    5              Chicão Vive   
..          ...  ...                      ...   
254         254  347           Metrô Brooklin   
255         255  354       Praça Oswaldo Cruz   
256         256  355  R. Dr. Rafael de Barros   
257         257  358     Shopping Villa Lobos   
258         258  359                     CENU   

                                             ENDEREÇO         lat  \
0    Av. Brigadeiro Faria Lima, esquina R. Teodoro ... -23.566831   
1      R. Ferreira de Araújo, em frente ao número 1031 -23.566920   
2    R. Gilberto Sabino, 138/ ao lado do ponto de ô... -23.566478   
3    Av. Brigadeiro Faria Lima, na altura do número... -23.569145   
4                                    Rua Butantã , 192 -23.569894   
..                                                 ...        ...   
254  Av. Santo Amaro, próximo ao acesso do metrô Br... -23.626894   
255                      Praça Oswaldo Cruz, oposto 97 -23.571604   
256  Rua Dr. Rafael de Barros, em frente ao 253 / P... -23.572712   
257                    Avenida das Nações Unidas, 4777 -23.551665   
258  Av das Nações Unidas, 12901/ Próximo à esquina... -23.609980   

                   lon  VAGAS/DOCK AGORA DATA INAUGURAÇÃO  
0    -46.6937412022694                83       2018-01-30  
1            -46.69819                15       2020-12-19  
2    -46.7012582819428                15       2018-01-30  
3    -46.6920025786078                23       2018-05-10  
4    -46.6978971886828                 7       2019-12-03  
..                 ...               ...              ...  
254  -46.6875731165835                29       2018-12-12  
255  -46.6442662143517                11       2019-12-21  
256  -46.6465303687604                19       2019-01-31  
257   -46.722562508944                 7       2018-12-12  
258    -46.69641184041                11       2018-12-05  

[259 rows x 8 columns]

In [6]:
stations[stations['lat'].isna()]

Empty DataFrame
Columns: [Unnamed: 0, id, NOME, ENDEREÇO , lat, lon, VAGAS/DOCK AGORA, DATA INAUGURAÇÃO]
Index: []

In [17]:
from modules.GeolocatorTomTom import *
import json

tomTomKey="gKJbocBwXPikRmcqAH42lchEFHAHhA3d"

def getCoordinates(location):
    geolocator = GeolocatorTomTom(tomTomKey)
    latitude, longitude = geolocator.getCoordinates(location)
    return (latitude,longitude)

In [18]:
getCoordinates("Rua Lourenço de Almeida, 36")

(-23.5954564, -46.668458)

In [19]:
getCoordinates("Rua Artur Etzel")

(-23.5788395, -46.6600902)

In [20]:
getCoordinates("Rua Cravinhos, 136")

(-23.5699035, -46.6618793)

In [21]:
stations['lat'][28]

nan

In [22]:
latitude, longitude = getCoordinates("Rua Lourenço de Almeida, 36")
stations['lat'][28] = latitude
stations['lon'][28] = longitude

latitude, longitude = getCoordinates("Rua Artur Etzel")
stations['lat'][37] = latitude
stations['lon'][37] = longitude

latitude, longitude = getCoordinates("Rua Cravinhos, 136")
stations['lat'][58] = latitude
stations['lon'][58] = longitude

/home/ana/Documents/ic/bss-analysis/virtualenv/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/home/ana/Documents/ic/bss-analysis/virtualenv/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
/home/ana/Documents/ic/bss-analysis/virtualenv/lib/python3.7/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.o

In [23]:
stations[stations['lat'].isna()]

Empty DataFrame
Columns: [id, NOME, ENDEREÇO , lat, lon, VAGAS/DOCK AGORA, DATA INAUGURAÇÃO]
Index: []

In [24]:
stations.to_csv('../data/stations/treated_data/2021.11.08_Endereços-BikeSAMPA.csv')

In [44]:
def convert_to_float(row):
    string_row = str(row)
    string_row = string_row.replace("'", "")
    return float(string_row)

stations['lat'] = stations['lat'].apply(convert_to_float)
stations['lon'] = stations['lon'].apply(convert_to_float)

In [26]:
from modules.GeolocatorTomTom import *

tomTomKey="gKJbocBwXPikRmcqAH42lchEFHAHhA3d"
geolocator = GeolocatorTomTom(tomTomKey)

In [36]:
df = pd.DataFrame(columns=['id_source','id_destination','distance'])
df

Empty DataFrame
Columns: [id_source, id_destination, distance]
Index: []

In [24]:
new_row = pd.Series({'id_source':1,'id_destination':2,'distance':3},name='station_pair')
df = df.append(new_row, ignore_index=True)
df

id_source id_destination distance
0         1              2        3
1         1              2        3

In [44]:
mode='bicycle'
df = pd.DataFrame(columns=['id_source','id_destination','distance_in_meters_bicycle','travel_time_in_seconds_bicycle'])

for i in range(len(stations)-255):
    for j in range(len(stations)-255):
        print("i = " + str(i) + " and j = "+str(j))

        id_src = stations['id'][i]
        id_dst = stations['id'][j]

        if j < i:
            # already computed
            print("already computed for i = " + str(i) + " and j = "+str(j))
            print(df)
            old_row = df.loc[(df['id_source'] == id_dst) & (df['id_destination'] == id_src)]
            print('old_row')
            print(old_row)

            print("virará source (igual i): ", old_row['id_destination'].values[0])

            new_row = pd.Series({'id_source': old_row['id_destination'].values[0],
                                'id_destination': old_row['id_source'].values[0],
                                'distance_in_meters_bicycle': old_row['distance_in_meters_bicycle'].values[0],
                                'travel_time_in_seconds_bicycle': old_row['travel_time_in_seconds_bicycle'].values[0] })
            df = df.append(new_row, ignore_index=True)
        else:
            src_latitude = stations['lat'][i]
            src_longitude = stations['lon'][i]
            dst_latitude = stations['lat'][j]
            dst_longitude = stations['lon'][j]

            response = geolocator.getDistanceFromCoordinates(src_latitude, src_longitude,
                                                        dst_latitude, dst_longitude, mode)

            if (response['code'] == 0):
                travel_time = response['travelTimeInSeconds']
                travel_distance = response['lengthInMeters']
            
            new_row = pd.Series({'id_source':id_src,
                                'id_destination':id_dst,
                                'distance_in_meters_bicycle':travel_distance,
                                'travel_time_in_seconds_bicycle':travel_time })
            df = df.append(new_row, ignore_index=True)

df
        

i = 0 and j = 0
i = 0 and j = 1
i = 0 and j = 2
i = 0 and j = 3
i = 1 and j = 0
already computed for i = 1 and j = 0
  id_source id_destination distance_in_meters_bicycle  \
0         1              1                          0   
1         1              2                        916   
2         1              3                       1082   
3         1              4                        348   

  travel_time_in_seconds_bicycle  
0                              0  
1                            186  
2                            205  
3                            109  
old_row
  id_source id_destination distance_in_meters_bicycle  \
1         1              2                        916   

  travel_time_in_seconds_bicycle  
1                            186  
virará source (igual i):  2
i = 1 and j = 1
i = 1 and j = 2
i = 1 and j = 3
i = 2 and j = 0
already computed for i = 2 and j = 0
  id_source id_destination distance_in_meters_bicycle  \
0         1              1                 

id_source id_destination distance_in_meters_bicycle  \
0          1              1                          0   
1          1              2                        916   
2          1              3                       1082   
3          1              4                        348   
4          2              1                        916   
5          2              2                          0   
6          2              3                        633   
7          2              4                        819   
8          3              1                       1082   
9          3              2                        633   
10         3              3                          0   
11         3              4                       1148   
12         4              1                        348   
13         4              2                        819   
14         4              3                       1148   
15         4              4                          0   

   travel_time_in_seconds_bicycle  
0                               0  
1                             186  
2                             205  
3                             109  
4                             186  
5                               0  
6                             123  
7                             193  
8                             205  
9                             123  
10                              0  
11                            213  
12                            109  
13                            193  
14                            213  
15                              0

In [52]:
mode='bicycle'
df = pd.DataFrame(columns=['id_source','id_destination','distance_in_meters_bicycle','travel_time_in_seconds_bicycle'])

for i in range(len(stations)):
    print("i =", i)
    for j in range(len(stations)):

        id_src = stations['id'][i]
        id_dst = stations['id'][j]

        src_latitude = stations['lat'][i]
        src_longitude = stations['lon'][i]
        dst_latitude = stations['lat'][j]
        dst_longitude = stations['lon'][j]

        response = geolocator.getDistanceFromCoordinates(src_latitude, src_longitude,
                                                    dst_latitude, dst_longitude, mode)

        if (response['code'] == 0):
            travel_time = response['travelTimeInSeconds']
            travel_distance = response['lengthInMeters']
        
        new_row = pd.Series({'id_source':id_src,
                            'id_destination':id_dst,
                            'distance_in_meters_bicycle':travel_distance,
                            'travel_time_in_seconds_bicycle':travel_time })
        df = df.append(new_row, ignore_index=True)
    df.to_csv('../data/stations/distance/stations_distance.csv')

df
        

i = 0
i = 1
i = 2
i = 3
Something went wrong while trying to send request to TomTom Expecting value: line 1 column 1 (char 0)
Something went wrong while trying to send request to TomTom Expecting value: line 1 column 1 (char 0)
Something went wrong while trying to send request to TomTom Expecting value: line 1 column 1 (char 0)
Something went wrong while trying to send request to TomTom Expecting value: line 1 column 1 (char 0)
Something went wrong while trying to send request to TomTom Expecting value: line 1 column 1 (char 0)
Something went wrong while trying to send request to TomTom Expecting value: line 1 column 1 (char 0)
Something went wrong while trying to send request to TomTom Expecting value: line 1 column 1 (char 0)
Something went wrong while trying to send request to TomTom Expecting value: line 1 column 1 (char 0)
Something went wrong while trying to send request to TomTom Expecting value: line 1 column 1 (char 0)
Something went wrong while trying to send request to TomTo

KeyboardInterrupt: 

In [ ]:
df.to_csv('../data/stations/distance/stations_distance.csv')

In [38]:
old_row = df.loc[(df['id_source'] == 2) & (df['id_destination'] == 3)]

new_row = pd.Series({'id_source': old_row['id_destination'].values[0],
                    'id_destination': old_row['id_source'].values[0],
                    'distance_in_meters_bicycle': old_row['distance_in_meters_bicycle'].values[0],
                    'travel_time_in_seconds_bicycle': old_row['travel_time_in_seconds_bicycle'].values[0] })
df = df.append(new_row, ignore_index=True)

In [39]:
df

id_source id_destination distance_in_meters_bicycle  \
0          1              1                          0   
1          1              2                        916   
2          1              3                       1082   
3          1              4                        348   
4          2              1                        613   
5          2              2                          0   
6          2              3                        633   
7          2              4                        819   
8          3              1                        942   
9          3              2                        493   
10         3              3                          0   
11         3              4                       1148   
12         4              1                        327   
13         4              2                       1243   
14         4              3                       1409   
15         4              4                          0   
16         3              2                        633   

   travel_time_in_seconds_bicycle  
0                               0  
1                             186  
2                             205  
3                             109  
4                             159  
5                               0  
6                             123  
7                             193  
8                             179  
9                              93  
10                              0  
11                            213  
12                             59  
13                            245  
14                            264  
15                              0  
16                            123

In [33]:
old_row = df.loc[(df['id_source'] == 2) & (df['id_destination'] == 1)]

In [37]:
old_row['id_destination'].values[0]

1

In [48]:
df

id_source  \
0                                            1   
1                                            1   
2                                            1   
3                                            1   
4                                            2   
5                                            2   
6                                            2   
7                                            2   
8                                            3   
9                                            3   
10                                           3   
11                                           3   
12                                           4   
13                                           4   
14                                           4   
15                                           4   
16  4    1
Name: id_destination, dtype: object   

                           id_destination distance_in_meters_bicycle  \
0                                       1                          0   
1                                       2                        916   
2                                       3                       1082   
3                                       4                        348   
4                                       1                        613   
5                                       2                          0   
6                                       3                        633   
7                                       4                        819   
8                                       1                        942   
9                                       2                        493   
10                                      3                          0   
11                                      4                       1148   
12                                      1                        327   
13                                      2                       1243   
14                                      3                       1409   
15                                      4                          0   
16  4    2
Name: id_source, dtype: object                          0   

   travel_time_in_seconds_bicycle  
0                               0  
1                             186  
2                             205  
3                             109  
4                             159  
5                               0  
6                             123  
7                             193  
8                             179  
9                              93  
10                              0  
11                            213  
12                             59  
13                            245  
14                            264  
15                              0  
16                              0

In [6]:
df.to_csv('../data/stations/distance/stations_distance.csv')

In [29]:
mode='bicycle'

i = 0
j = 1
        
src_latitude = stations['lat'][i]
src_longitude = stations['lon'][i]
dst_latitude = stations['lat'][j]
dst_longitude = stations['lon'][j]

response = geolocator.getDistanceFromCoordinates(src_latitude, src_longitude,
                                            dst_latitude, dst_longitude, mode)

if (response['code'] == 0):
    print(response)
    travel_time = response['travelTimeInSeconds']
    travel_distance = response['lengthInMeters']

mode='car'

i = 0
j = 1
        
src_latitude = stations['lat'][i]
src_longitude = stations['lon'][i]
dst_latitude = stations['lat'][j]
dst_longitude = stations['lon'][j]

response = geolocator.getDistanceFromCoordinates(src_latitude, src_longitude,
                                            dst_latitude, dst_longitude, mode)

if (response['code'] == 0):
    print(response)
    travel_time = response['travelTimeInSeconds']
    travel_distance = response['lengthInMeters']

{'code': 0, 'lengthInMeters': 916, 'travelTimeInSeconds': 186}
{'code': 0, 'lengthInMeters': 1401, 'travelTimeInSeconds': 230}


In [46]:
mode='bicycle'

i = 0
j = 1
        
src_latitude = stations['lat'][i]
src_longitude = stations['lon'][i]
dst_latitude = stations['lat'][j]
dst_longitude = stations['lon'][j]

response = geolocator.getDistanceFromCoordinates(src_latitude, src_longitude,
                                            dst_latitude, dst_longitude, mode)

if (response['code'] == 0):
    print(response)
    travel_time = response['travelTimeInSeconds']
    travel_distance = response['lengthInMeters']

i = 1
j = 0
        
src_latitude = stations['lat'][i]
src_longitude = stations['lon'][i]
dst_latitude = stations['lat'][j]
dst_longitude = stations['lon'][j]

response = geolocator.getDistanceFromCoordinates(src_latitude, src_longitude,
                                            dst_latitude, dst_longitude, mode)

if (response['code'] == 0):
    print(response)
    travel_time = response['travelTimeInSeconds']
    travel_distance = response['lengthInMeters']

{'code': 0, 'lengthInMeters': 916, 'travelTimeInSeconds': 186}
{'code': 0, 'lengthInMeters': 613, 'travelTimeInSeconds': 159}


In [27]:
source = 'IME'
destination = 'MASP'
mode='bicycle'

response = geolocator.getRoute(source, destination, mode)

if (response['code'] == 0):
    travelTime = response['travelTime']
    print(response)

{'code': 0, 'travelTime': 1874, 'routePoints': [[-46.7316, -23.55906], [-46.73117, -23.55909], [-46.73108, -23.55911], [-46.73102, -23.55913], [-46.73099, -23.55917], [-46.73098, -23.55921], [-46.73098, -23.55938], [-46.73097, -23.55943], [-46.73096, -23.55947], [-46.73093, -23.5595], [-46.73091, -23.55952], [-46.73079, -23.55957], [-46.73077, -23.55959], [-46.73075, -23.55961], [-46.73074, -23.55963], [-46.73074, -23.55965], [-46.73074, -23.5597], [-46.73075, -23.55975], [-46.73076, -23.55978], [-46.73094, -23.56005], [-46.73095, -23.56008], [-46.73095, -23.5601], [-46.73094, -23.56012], [-46.73092, -23.56014], [-46.7309, -23.56016], [-46.73088, -23.56016], [-46.73043, -23.56037], [-46.73058, -23.56057], [-46.73137, -23.5602], [-46.73139, -23.56014], [-46.73145, -23.56009], [-46.73153, -23.56004], [-46.73173, -23.55999], [-46.73186, -23.56], [-46.73223, -23.55993], [-46.73239, -23.55993], [-46.73262, -23.55989], [-46.73267, -23.55982], [-46.73274, -23.55965], [-46.73275, -23.55957], [

In [52]:
stations.loc[117]

Unnamed: 0                                                        117
id                                                                140
NOME                                                      JK Iguatemi
ENDEREÇO            Av. Pres. Juscelino Kubitschek, esquina com Av...
lat                                                        -23.590748
lon                                                        -46.688863
VAGAS/DOCK AGORA                                                   19
DATA INAUGURAÇÃO                                           2018-12-07
Name: 117, dtype: object

In [12]:
import json
import requests

st1 = stations.loc[0]
st2 = stations.loc[1]


graph_hopper_key = 'bb4601e7-696d-4b91-a809-4b1b8256b2a8'
data = json.dumps({'out_arrays': ['distances'], 'from_points': [[str(st1['lon']),str(st1['lat'])]], 
                                   'to_points': [[str(st2['lon']),str(st2['lat'])]], 'vehicle': 'bike'})
req = requests.post("https://graphhopper.com/api/1/matrix?key=" + graph_hopper_key, 
                    headers={'Content-Type': 'application/json'}, data=data)
print(req.status_code, req.reason)
if req.status_code == 200:
    print([st1['id'],st2['id']])
    print(st1['id'],st2['id'],((req.json()['distances'])[0][0])/1000)

200 OK
[1, 2]
1 2 1.268


In [20]:
import json
import requests

st1 = stations.loc[1]
st2 = stations.loc[0]


graph_hopper_key = 'bb4601e7-696d-4b91-a809-4b1b8256b2a8'
data = json.dumps({'out_arrays': ['distances'], 'from_points': [[str(st1['lon']),str(st1['lat'])]], 
                                   'to_points': [[str(st2['lon']),str(st2['lat'])]], 'vehicle': 'bike'})

req = requests.post("https://graphhopper.com/api/1/matrix?key=" + graph_hopper_key, 
                    headers={'Content-Type': 'application/json'}, data=data)

print(req.status_code, req.reason)
if req.status_code == 200:
    print([st1['id'],st2['id']])
    print(req.json())
    print(st1['id'],st2['id'],((req.json()['distances'])[0][0]))

200 OK
[2, 1]
{'distances': [[1267]], 'info': {'copyrights': ['GraphHopper', 'OpenStreetMap contributors']}}
2 1 1267


In [ ]:
st1 = stations.loc[i]
st2 = stations.loc[j]

data = json.dumps({'out_arrays': ['distances'], 'from_points': [[str(['lon']),str(st1['lat'])]], 
                                'to_points': [[str(st2['lon']),str(st2['lat'])]], 'vehicle': 'bike'})

response = requests.post("https://graphhopper.com/api/1/matrix?key=" + graph_hopper_key, 
                    headers={'Content-Type': 'application/json'}, data=data)

travel_distance = -1

if response.status_code == 200:
    travel_distance = response.json()['distances'][0][0]

In [23]:
len(stations)

259

In [64]:
stations[stations['id'] == 142]

Unnamed: 0   id      NOME  \
119         119  142  Minhocão   

                                             ENDEREÇO         lat        lon  \
119  Av. Gen. Olímpio da Silveira, nº 324 / na Praç... -23.531743 -46.659187   

     VAGAS/DOCK AGORA DATA INAUGURAÇÃO  
119                15       2021-08-27

In [66]:
graph_hopper_key = '1c44c2ec-e5af-4a3e-8152-db3777387440'
df = pd.DataFrame(columns=['id_source','id_destination','distance_in_meters_bicycle'])
error_df = pd.DataFrame(columns=['id_source','id_destination','error'])

for i in range(87, 88):
    print("i =", i)
    for j in range(119, 120):

        st1 = stations.loc[i]
        st2 = stations.loc[j]

        data = json.dumps({'out_arrays': ['distances'], 'from_points': [[str(st1['lon']),str(st1['lat'])]], 
                                   'to_points': [[str(st2['lon']),str(st2['lat'])]], 'vehicle': 'bike'})

        response = requests.post("https://graphhopper.com/api/1/matrix?key=" + graph_hopper_key, 
                    headers={'Content-Type': 'application/json'}, data=data)
        
        travel_distance = -1

        if response.status_code == 200:
            travel_distance = response.json()['distances'][0][0]
        else:
            new_row = pd.Series({'id_source':st1['id'],
                            'id_destination':st2['id'],
                            'error': str(response.status_code) + ' ' + str(response.reason)})
            error_df = error_df.append(new_row, ignore_index=True)
        
        new_row = pd.Series({'id_source':st1['id'],
                            'id_destination':st2['id'],
                            'distance_in_meters_bicycle': travel_distance})
        df = df.append(new_row, ignore_index=True)
    df.to_csv('../data/stations/distance/stations_distance6.csv')

error_df.to_csv('../data/stations/distance/error_stations_distance6.csv')
df.to_csv('../data/stations/distance/stations_distance6.csv')
        

i = 87


In [59]:
stations[stations['id'] == 138]

Unnamed: 0   id    NOME  \
116         116  138  Chilon   

                                             ENDEREÇO         lat        lon  \
116  Rua Chilon, em frente ao número 642 da R. Prof... -23.593601 -46.680072   

     VAGAS/DOCK AGORA DATA INAUGURAÇÃO  
116                23       2018-12-08

In [61]:
stations.loc[117]

Unnamed: 0                                                        117
id                                                                140
NOME                                                      JK Iguatemi
ENDEREÇO            Av. Pres. Juscelino Kubitschek, esquina com Av...
lat                                                        -23.590748
lon                                                        -46.688863
VAGAS/DOCK AGORA                                                   19
DATA INAUGURAÇÃO                                           2018-12-07
Name: 117, dtype: object

In [37]:
df

id_source id_destination distance_in_meters_bicycle
0         1              1                          0
1         1              2                       1268
2         2              1                       1267
3         2              2                          0

In [40]:
error_df

id_source id_destination                  error
0             1            206        400 Bad Request
1             2            206        400 Bad Request
2             3            206        400 Bad Request
3             4            206        400 Bad Request
4             5            206        400 Bad Request
...         ...            ...                    ...
17916       217            193  429 Too Many Requests
17917       217            194  429 Too Many Requests
17918       217            196  429 Too Many Requests
17919       217            197  429 Too Many Requests
17920       217            198  429 Too Many Requests

[17921 rows x 3 columns]

In [8]:
stations_distance = pd.read_csv('../data/stations/distance/stations_distance.csv')
stations_distance

Unnamed: 0  id_source  id_destination  distance_in_meters_bicycle
0               0          1               1                           0
1               1          1               2                        1268
2               2          1               3                        1158
3               3          1               4                         358
4               4          1               5                        1631
...           ...        ...             ...                         ...
67076       11391        359             347                        2969
67077       11392        359             354                        8524
67078       11393        359             355                        8098
67079       11394        359             358                        8766
67080       11395        359             359                           0

[67081 rows x 4 columns]

In [17]:
stations_distance = stations_distance.drop('Unnamed: 0', axis = 1)
stations_distance

id_source  id_destination  distance_in_meters_bicycle
0              1               1                           0
1              1               2                        1268
2              1               3                        1158
3              1               4                         358
4              1               5                        1631
...          ...             ...                         ...
67076        359             347                        2969
67077        359             354                        8524
67078        359             355                        8098
67079        359             358                        8766
67080        359             359                           0

[67081 rows x 3 columns]

In [18]:
stations_distance.to_csv('../data/stations/distance/stations_distance.csv', index=False)

In [16]:
stations_distance = pd.read_csv('../data/stations/distance/stations_distance.csv')
stations_distance

Unnamed: 0  id_source  id_destination  distance_in_meters_bicycle
0               0          1               1                           0
1               1          1               2                        1268
2               2          1               3                        1158
3               3          1               4                         358
4               4          1               5                        1631
...           ...        ...             ...                         ...
67076       67076        359             347                        2969
67077       67077        359             354                        8524
67078       67078        359             355                        8098
67079       67079        359             358                        8766
67080       67080        359             359                           0

[67081 rows x 4 columns]